In [90]:
# Importing Libraries

import requests
from bs4 import BeautifulSoup 
import re
# import library for date
from datetime import datetime, timedelta
import time

import json
import pandas as pd

In [95]:
# Error handling function while loading the site and
# Defining the Header for using User-Agent approach to have access to the site info

HEADER = {
    "User-Agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/141.0.0.0 Safari/537.36"
}


def make_connection(url):
    """ Make a request to http url
    and return a beautiful soup object"""
    try:
        response = requests.get(url, headers=HEADER)
        if response.status_code == 200:
            soup_content = BeautifulSoup(response.content, 'html.parser')
            return soup_content
        else:
            print(f"Resources Not available! Status Code {response.status_code}")
    except Exception as e:
        print(f"An Error occurs. Message: {e}")

# Property image url
def extract_image_url(property_info):
    img_tag = property_info.find('img')
    if not img_tag:
        return None
    
    return img_tag.get('data-src') or img_tag.get('src')

# Extract amenities 
def property_amenities(property_info):
    amenities = {"bedrooms": "N/A", "bathrooms": "N/A", "toilets": "N/A"}
    
    amenity = property_info.find("ul", class_="property-benefit")
    if not amenity:
        return amenities
    
    amenity_tags = amenity.find_all("li")
    
    # Use index positions
    if len(amenity_tags) >= 1:
        text = amenity_tags[0].get_text(strip=True)
        amenities["bedrooms"] = int(text) if text.isdigit() else "N/A"
    if len(amenity_tags) >= 2:
        text = amenity_tags[1].get_text(strip=True)
        amenities["bathrooms"] = int(text) if text.isdigit() else "N/A"
    if len(amenity_tags) >= 3:
        text = amenity_tags[2].get_text(strip=True)
        amenities["toilets"] = int(text) if text.isdigit() else "N/A"
    
    return amenities

# property date
property_date = property_info.find("div", class_= "media-body").find('h5')
raw_date = property_date.get_text(strip=True) if property_date else ""
def normalize_date(raw_date: str) -> dict:
    """
    Normalize property date strings when both Updated and Added
    are in the same span.
    """
    raw_date = raw_date.lower()
    today = datetime.today()
    result = {"updated_date": None, "added_date": None}
    
    # Handle relative dates first
    if "updated today" in raw_date:
        result["updated_date"] = today.strftime("%Y-%m-%d")
    elif "updated yesterday" in raw_date:
        result["updated_date"] = (today - timedelta(days=1)).strftime("%Y-%m-%d")
    
    # Handle absolute dates (both updated and added in same string)
    parts = raw_date.split(",")
    for part in parts:
        part = part.strip()
        if part.startswith("updated"):
            date_str = part.replace("updated", "").strip()
            try:
                result["updated_date"] = datetime.strptime(date_str, "%d %b %Y").strftime("%Y-%m-%d")
            except:
                pass
        elif part.startswith("added"):
            date_str = part.replace("added", "").strip()
            try:
                result["added_date"] = datetime.strptime(date_str, "%d %b %Y").strftime("%Y-%m-%d")
            except:
                pass
    
    return result


def scrap_page_property(properties_info):
    """
    scrap single page property to return list of dictionary
    """
    single_page_property= []
    
    for property_info in properties_info:
        property_title_div= property_info.find("div", class_= "similar-listings-info").find('h2')
        property_title= property_title_div.get_text() if property_title_div is not None else "N/A"

        listing_type_div= property_info.find("div", class_= "similar-listings-info").find('h3')
        listing_type = listing_type_div.get_text() if listing_type_div is not None else "N/A"
        
        property_type_div= property_info.find("div", class_= "similar-listings-info").find('h2')
        property_type = property_type_div.get_text() if property_type_div is not None else "N/A"
        
        property_price_div= property_info.find("div", class_= "similar-listings-price").find('h4')
        property_price= property_price_div.get_text()if property_price_div is not None else "N/A"  
        
        property_price_currency_div= property_info.find("div", class_= "similar-listings-price").find('span')
        property_price_currency= property_price_currency_div.get_text()if property_price_currency_div is not None else "N/A"  

        amenities = property_amenities(property_info)
         
        property_location_div= property_info.find("div", class_= "similar-listings-info").find('p')
        property_location= property_location_div.get_text()if property_location_div is not None else "N/A" 

        property_agent_name_div = property_info.find('div', class_="media").find('img')
        property_agent_name= property_agent_name_div.get('alt') if property_location_div is not None else "N/A"
        
        Property_agent_link_div= property_info.find('div', class_='similar-listing-contact').find('a')
        Property_agent_link= Property_agent_link_div.get('href') if Property_agent_link_div is not None else "N/A"

        property_date_div = property_info.find("div", class_= "media-body").find('h5')
        raw_date = property_date_div.get_text(strip=True) if property_date_div else ""
        dates = normalize_date(raw_date)
        
        img_url = extract_image_url(property_info)

        favorites_div = property_info.find('a', class_="listings-favorite")
        favorites = favorites_div.get('href') if favorites_div is not None else "N/A"

        
    
        single_property = {
            "title": property_title,
            "listing_type": listing_type,
            "property_type": property_type,
            "price": property_price,
            "currency": property_price_currency,
            "bedrooms": amenities["bedrooms"],
            "bathrooms": amenities["bathrooms"],
            "toilets": amenities["toilets"],
            "location": property_location,
            "agent_name": property_agent_name,
            "agent_link": Property_agent_link,
            "date": dates,
            "image_url": img_url,
            "favorite": favorites
        }
        single_page_property.append(single_property)
    
    return single_page_property
        

In [96]:
# all properties
all_property = {}

# all pages of website
for page_num in range(1,137):
    # website URL
    URL = f"https://privateproperty.ng/property-for-rent?page={page_num}"
    print(f"Scrapping property data from page {page_num}")

    # make connection
    soup_content = make_connection(URL)

    # single page property 
    properties_info = soup_content.find_all("div", class_="similar-listings-item" )
    
    single_page_property = scrap_page_property(properties_info)
    print(f"Property Scrapped successfully: {len(single_page_property)} properties Retrived")

     # sleep
    time.sleep(10)  
    
    all_property.update({f"page {page_num}":single_page_property})

Scrapping property data from page 1
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 2
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 3
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 4
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 5
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 6
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 7
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 8
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 9
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 10
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 11
Property Scrapped successfully: 22 properties Retriv

In [97]:
all_property

{'page 1': [{'title': 'Exquisite 4 Bedroom Terrace Duplex With Bq.',
   'listing_type': '4 BEDROOM TERRACED DUPLEX For Rent',
   'property_type': 'Exquisite 4 Bedroom Terrace Duplex With Bq.',
   'price': '₦ 35,000,000/year',
   'currency': '₦',
   'bedrooms': 4,
   'bathrooms': 4,
   'toilets': 5,
   'location': '\n\n\n Parkview Ikoyi Parkview Estate Ikoyi Lagos',
   'agent_name': 'Torysrealty',
   'agent_link': '/estate-agents/torysrealty',
   'date': {'updated_date': '2025-12-02', 'added_date': None},
   'image_url': 'https://images.privateproperty.com.ng/medium/exquisite-4-bedroom-terrace-duplex-with-bq-r7RJdW2sgGpNsiXd4oUa.jpg',
   'favorite': '/profile/add-favorite/48634045'},
  {'title': 'Fully Furnished & Serviced 4 Bedroom Semi Detached Duplex',
   'listing_type': '4 BEDROOM SEMI DETACHED DUPLEX FOR RENT',
   'property_type': 'Fully Furnished & Serviced 4 Bedroom Semi Detached Duplex',
   'price': '₦ 15,000,000',
   'currency': '₦',
   'bedrooms': 4,
   'bathrooms': 4,
   'toi

In [99]:
len(all_property)

136

/* 
-property_title= property_info.find("div", class_= "similar-listings-info").find('h2').get_text()
-listing_type= property_info.find("div", class_= "similar-listings-info").find('h3').get_text()
-property_type= property_info.find("div", class_= "similar-listings-info").find('h2').get_text()
-property_price= property_info.find("div", class_= "similar-listings-price").find('h4').get_text()
-property_price_currency= property_info.find("div", class_= "similar-listings-price").find('span').get_text()
-amenities = property_amenities(property_info)
-property_location=property_info.find("div", class_= "similar-listings-info").find('p').get_text()
-property_agent_name = property_info.find('div', class_="media").find('img').get('alt')
-Property_agent_link= property_info.find('div', class_='similar-listing-contact').find('a').get('href')
-property_date= property_info.find("div", class_= "media-body").find('h5').get_text()
-img_url = extract_image_url(property_info)
-favorites = property_info.find('a', class_="listings-favorite").get('href') */

# To save it into the json file

In [100]:
data_rent = all_property
# Save to JSON
with open("../data/properties.json", "w", encoding="utf-8") as f:
    json.dump(data_rent, f, indent=4, ensure_ascii=False)

In [102]:
# to view the raw data
with open("../data/properties.json", "r", encoding="utf-8") as f:
    data_rent = json.load(f)

print(json.dumps(data_rent, indent=4, ensure_ascii=False))

{
    "page 1": [
        {
            "title": "Exquisite 4 Bedroom Terrace Duplex With Bq.",
            "listing_type": "4 BEDROOM TERRACED DUPLEX For Rent",
            "property_type": "Exquisite 4 Bedroom Terrace Duplex With Bq.",
            "price": "₦ 35,000,000/year",
            "currency": "₦",
            "bedrooms": 4,
            "bathrooms": 4,
            "toilets": 5,
            "location": "\n\n\n Parkview Ikoyi Parkview Estate Ikoyi Lagos",
            "agent_name": "Torysrealty",
            "agent_link": "/estate-agents/torysrealty",
            "date": {
                "updated_date": "2025-12-02",
                "added_date": null
            },
            "image_url": "https://images.privateproperty.com.ng/medium/exquisite-4-bedroom-terrace-duplex-with-bq-r7RJdW2sgGpNsiXd4oUa.jpg",
            "favorite": "/profile/add-favorite/48634045"
        },
        {
            "title": "Fully Furnished & Serviced 4 Bedroom Semi Detached Duplex",
            "list

In [104]:
# To flattened the pages into a single list instead of showing page number as title
# Load the JSON file
with open("../data/properties.json", "r", encoding="utf-8") as f:
    properties_page = json.load(f)

all_properties = []

# Flatten across pages AND flatten nested "date" to separate fields as updated and added
for page, listings in properties_page.items():
    for prop in listings:
        flat = prop.copy()
        # Pull nested date fields up
        if "date" in prop:
            flat["updated_date"] = prop["date"].get("updated_date")
            flat["added_date"] = prop["date"].get("added_date")
            del flat["date"]
        all_properties.append(flat)

# Now all_properties is a flat list of property dicts
# Preview first few results
print(json.dumps(all_properties[:5], indent=4, ensure_ascii=False))


[
    {
        "title": "Exquisite 4 Bedroom Terrace Duplex With Bq.",
        "listing_type": "4 BEDROOM TERRACED DUPLEX For Rent",
        "property_type": "Exquisite 4 Bedroom Terrace Duplex With Bq.",
        "price": "₦ 35,000,000/year",
        "currency": "₦",
        "bedrooms": 4,
        "bathrooms": 4,
        "toilets": 5,
        "location": "\n\n\n Parkview Ikoyi Parkview Estate Ikoyi Lagos",
        "agent_name": "Torysrealty",
        "agent_link": "/estate-agents/torysrealty",
        "image_url": "https://images.privateproperty.com.ng/medium/exquisite-4-bedroom-terrace-duplex-with-bq-r7RJdW2sgGpNsiXd4oUa.jpg",
        "favorite": "/profile/add-favorite/48634045",
        "updated_date": "2025-12-02",
        "added_date": null
    },
    {
        "title": "Fully Furnished & Serviced 4 Bedroom Semi Detached Duplex",
        "listing_type": "4 BEDROOM SEMI DETACHED DUPLEX FOR RENT",
        "property_type": "Fully Furnished & Serviced 4 Bedroom Semi Detached Duplex",


In [113]:
# Load the flattened JSON file as a clean table
# Load the original JSON
with open("../data/properties.json", "r", encoding="utf-8") as f:
    properties_page = json.load(f)

# Flatten across pages
all_properties = []
for page, listings in properties_page.items():
    for prop in listings:
        flat = prop.copy()
        # Flatten nested "date" dictionary if present
        if "date" in prop:
            flat["updated_date"] = prop["date"].get("updated_date")
            flat["added_date"] = prop["date"].get("added_date")
            del flat["date"]
        all_properties.append(flat)

# Convert to DataFrame
df = pd.DataFrame(all_properties)

# Preview the clean table
df.head(10)


title  \
0        Exquisite 4 Bedroom Terrace Duplex With Bq.   
1  Fully Furnished & Serviced 4 Bedroom Semi Deta...   
2    Charming And Fully Serviced 2 Bedroom Apartment   
3  Newly Built Spacious Selfcon With 24/7 Solar P...   
4  5 Bedroom Semi Detached Duplex With Bq. N10m Y...   
5          Mini Flat Apartment. N6.5m Yearly. Ikate.   
6             Exquisite 3 Bedroom Apartment With Bq.   
7    A Massive And Luxurious 5bedroom Terrace Duplex   
8                  Office Space On 4 Floors For Rent   
9         Luxurious 4 Bedroom Terrace Duplex With Bq   

                              listing_type  \
0       4 BEDROOM TERRACED DUPLEX For Rent   
1  4 BEDROOM SEMI DETACHED DUPLEX FOR RENT   
2        2 BEDROOM BLOCK OF FLATS FOR RENT   
3          1 BEDROOM SELF CONTAIN FOR RENT   
4  5 BEDROOM SEMI DETACHED DUPLEX FOR RENT   
5             1 BEDROOM MINI FLAT FOR RENT   
6      3 BEDROOM FLAT & APARTMENT FOR RENT   
7       5 BEDROOM TERRACED DUPLEX FOR RENT   
8                          OFFICE FOR RENT   
9       4 BEDROOM TERRACED DUPLEX FOR RENT   

                                       property_type              price  \
0        Exquisite 4 Bedroom Terrace Duplex With Bq.  ₦ 35,000,000/year   
1  Fully Furnished & Serviced 4 Bedroom Semi Deta...       ₦ 15,000,000   
2    Charming And Fully Serviced 2 Bedroom Apartment  ₦ 15,000,000/year   
3  Newly Built Spacious Selfcon With 24/7 Solar P...          ₦ 600,000   
4  5 Bedroom Semi Detached Duplex With Bq. N10m Y...  ₦ 10,000,000/year   
5          Mini Flat Apartment. N6.5m Yearly. Ikate.   ₦ 6,500,000/year   
6             Exquisite 3 Bedroom Apartment With Bq.  ₦ 15,000,000/year   
7    A Massive And Luxurious 5bedroom Terrace Duplex       ₦ 15,000,000   
8                  Office Space On 4 Floors For Rent      ₦ 140,000/sqm   
9         Luxurious 4 Bedroom Terrace Duplex With Bq   ₦ 8,000,000/year   

  currency bedrooms bathrooms toilets  \
0        ₦        4         4       5   
1        ₦        4         4       5   
2        ₦        2         2       3   
3        ₦        1         1       1   
4        ₦        5         5       6   
5        ₦        1         1       1   
6        ₦        3         3       4   
7        ₦        5         5       6   
8        ₦      N/A       N/A     N/A   
9        ₦        4         4       5   

                                            location  \
0  \n\n\n Parkview Ikoyi Parkview Estate Ikoyi Lagos   
1        \n\n\n Harris Drive, Beside Vgc Lekki Lagos   
2  \n\n\n Periwinkle Estate Lekki Phase 1 Lekki L...   
3                   \n\n\n Alatise Ibeju Lekki Lagos   
4  \n\n\n Chevron Drive Lekki Chevron Drive Lekki...   
5  \n\n\n Ikate Lekki Phase 1 Ikate Elegushi Lekk...   
6  \n\n\n Castle And Temple, Lekki Phase 1 Lekki ...   
7           \n\n\n Guzape Guzape Abuja Phase 1 Abuja   
8                    \n\n\n Allen Avenue Ikeja Lagos   
9     \n\n\n Thomas Estate Lekki Phase 2 Lekki Lagos   

                   agent_name                                  agent_link  \
0                 Torysrealty                  /estate-agents/torysrealty   
1         Bluehedge Realtors       /estate-agents/bluehedgerealtorsestate   
2         Bluehedge Realtors       /estate-agents/bluehedgerealtorsestate   
3     Core Real Estate World   /estate-agents/corerealestateinvestmentltd   
4                 Torysrealty                  /estate-agents/torysrealty   
5                 Torysrealty                  /estate-agents/torysrealty   
6                 Torysrealty                  /estate-agents/torysrealty   
7  O3 Intellectual Properties     /estate-agents/o3intellectualproperties   
8            Loyalty Property          /estate-agents/loyaltyhomeslimited   
9                 Torysrealty                  /estate-agents/torysrealty   

                                           image_url  \
0  https://images.privateproperty.com.ng/medium/e...   
1  https://images.privateproperty.com.ng/medium/f...   
2  https://i

In [110]:
# Save flattened version into a new JSON file
with open("../data/flattened_properties.json", "w", encoding="utf-8") as f:
    json.dump(all_properties, f, indent=4, ensure_ascii=False)

print("Flattened JSON saved successfully!")


Flattened JSON saved successfully!


In [111]:
# Load the flattened JSON file
with open("../data/flattened_properties.json", "r", encoding="utf-8") as f:
    all_properties = json.load(f)

# Convert to a DataFrame (table view)
df = pd.DataFrame(all_properties)

# Preview the first 5 rows
df.head(10)

title  \
0        Exquisite 4 Bedroom Terrace Duplex With Bq.   
1  Fully Furnished & Serviced 4 Bedroom Semi Deta...   
2    Charming And Fully Serviced 2 Bedroom Apartment   
3  Newly Built Spacious Selfcon With 24/7 Solar P...   
4  5 Bedroom Semi Detached Duplex With Bq. N10m Y...   
5          Mini Flat Apartment. N6.5m Yearly. Ikate.   
6             Exquisite 3 Bedroom Apartment With Bq.   
7    A Massive And Luxurious 5bedroom Terrace Duplex   
8                  Office Space On 4 Floors For Rent   
9         Luxurious 4 Bedroom Terrace Duplex With Bq   

                              listing_type  \
0       4 BEDROOM TERRACED DUPLEX For Rent   
1  4 BEDROOM SEMI DETACHED DUPLEX FOR RENT   
2        2 BEDROOM BLOCK OF FLATS FOR RENT   
3          1 BEDROOM SELF CONTAIN FOR RENT   
4  5 BEDROOM SEMI DETACHED DUPLEX FOR RENT   
5             1 BEDROOM MINI FLAT FOR RENT   
6      3 BEDROOM FLAT & APARTMENT FOR RENT   
7       5 BEDROOM TERRACED DUPLEX FOR RENT   
8                          OFFICE FOR RENT   
9       4 BEDROOM TERRACED DUPLEX FOR RENT   

                                       property_type              price  \
0        Exquisite 4 Bedroom Terrace Duplex With Bq.  ₦ 35,000,000/year   
1  Fully Furnished & Serviced 4 Bedroom Semi Deta...       ₦ 15,000,000   
2    Charming And Fully Serviced 2 Bedroom Apartment  ₦ 15,000,000/year   
3  Newly Built Spacious Selfcon With 24/7 Solar P...          ₦ 600,000   
4  5 Bedroom Semi Detached Duplex With Bq. N10m Y...  ₦ 10,000,000/year   
5          Mini Flat Apartment. N6.5m Yearly. Ikate.   ₦ 6,500,000/year   
6             Exquisite 3 Bedroom Apartment With Bq.  ₦ 15,000,000/year   
7    A Massive And Luxurious 5bedroom Terrace Duplex       ₦ 15,000,000   
8                  Office Space On 4 Floors For Rent      ₦ 140,000/sqm   
9         Luxurious 4 Bedroom Terrace Duplex With Bq   ₦ 8,000,000/year   

  currency bedrooms bathrooms toilets  \
0        ₦        4         4       5   
1        ₦        4         4       5   
2        ₦        2         2       3   
3        ₦        1         1       1   
4        ₦        5         5       6   
5        ₦        1         1       1   
6        ₦        3         3       4   
7        ₦        5         5       6   
8        ₦      N/A       N/A     N/A   
9        ₦        4         4       5   

                                            location  \
0  \n\n\n Parkview Ikoyi Parkview Estate Ikoyi Lagos   
1        \n\n\n Harris Drive, Beside Vgc Lekki Lagos   
2  \n\n\n Periwinkle Estate Lekki Phase 1 Lekki L...   
3                   \n\n\n Alatise Ibeju Lekki Lagos   
4  \n\n\n Chevron Drive Lekki Chevron Drive Lekki...   
5  \n\n\n Ikate Lekki Phase 1 Ikate Elegushi Lekk...   
6  \n\n\n Castle And Temple, Lekki Phase 1 Lekki ...   
7           \n\n\n Guzape Guzape Abuja Phase 1 Abuja   
8                    \n\n\n Allen Avenue Ikeja Lagos   
9     \n\n\n Thomas Estate Lekki Phase 2 Lekki Lagos   

                   agent_name                                  agent_link  \
0                 Torysrealty                  /estate-agents/torysrealty   
1         Bluehedge Realtors       /estate-agents/bluehedgerealtorsestate   
2         Bluehedge Realtors       /estate-agents/bluehedgerealtorsestate   
3     Core Real Estate World   /estate-agents/corerealestateinvestmentltd   
4                 Torysrealty                  /estate-agents/torysrealty   
5                 Torysrealty                  /estate-agents/torysrealty   
6                 Torysrealty                  /estate-agents/torysrealty   
7  O3 Intellectual Properties     /estate-agents/o3intellectualproperties   
8            Loyalty Property          /estate-agents/loyaltyhomeslimited   
9                 Torysrealty                  /estate-agents/torysrealty   

                                           image_url  \
0  https://images.privateproperty.com.ng/medium/e...   
1  https://images.privateproperty.com.ng/medium/f...   
2  https://i

# Property for Sale

In [157]:
# Error handling function while loading the site and
# Defining the Header for using User-Agent approach to have access to the site info

URL = "https://privateproperty.ng/property-for-sale"
HEADER = {
    "User-Agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/141.0.0.0 Safari/537.36"
}

def make_connection_now(url):
    try:
        response = requests.get(url, headers=HEADER)
        if response.status_code == 200:
            soup_contents = BeautifulSoup(response.content, 'html.parser')
            return soup_contents
        else:
            print(f"Resources Not available! Status Code {response.status_code}")
    except Exception as e:
        print(f"An Error occurs. Message: {e}")

# Property image url
def extract_image_url(property_info_div):
    img_tag = property_info.find('img')
    if not img_tag:
        return None
    
    return img_tag.get('data-src') or img_tag.get('src')

# Extract amenities 
def property_amenities(property_info_div):
    amenities = {"bedrooms": "N/A", "bathrooms": "N/A", "toilets": "N/A"}
    
    amenity = property_info_div.find("ul", class_="property-benefit")
    if not amenity:
        return amenities
    
    amenity_tags = amenity.find_all("li")
    
    # Use index positions
    if len(amenity_tags) >= 1:
        text = amenity_tags[0].get_text(strip=True)
        amenities["bedrooms"] = int(text) if text.isdigit() else "N/A"
    if len(amenity_tags) >= 2:
        text = amenity_tags[1].get_text(strip=True)
        amenities["bathrooms"] = int(text) if text.isdigit() else "N/A"
    if len(amenity_tags) >= 3:
        text = amenity_tags[2].get_text(strip=True)
        amenities["toilets"] = int(text) if text.isdigit() else "N/A"
    
    return amenities

# property date
property_date = property_info_div.find("div", class_= "media-body").find('h5')
raw_date = property_date.get_text(strip=True) if property_date else ""
def normalize_date_div(raw_date: str) -> dict:
    """
    Normalize property date strings when both Updated and Added
    are in the same span.
    """
    raw_date = raw_date.lower()
    today = datetime.today()
    result = {"updated_date": None, "added_date": None}
    
    # Handle relative dates first
    if "updated today" in raw_date:
        result["updated_date"] = today.strftime("%Y-%m-%d")
    elif "updated yesterday" in raw_date:
        result["updated_date"] = (today - timedelta(days=1)).strftime("%Y-%m-%d")
    
    # Handle absolute dates (both updated and added in same string)
    parts = raw_date.split(",")
    for part in parts:
        part = part.strip()
        if part.startswith("updated"):
            date_str = part.replace("updated", "").strip()
            try:
                result["updated_date"] = datetime.strptime(date_str, "%d %b %Y").strftime("%Y-%m-%d")
            except:
                pass
        elif part.startswith("added"):
            date_str = part.replace("added", "").strip()
            try:
                result["added_date"] = datetime.strptime(date_str, "%d %b %Y").strftime("%Y-%m-%d")
            except:
                pass
    
    return result

# scrap all peoperties
def scrap_page_saproperty(property_info_div):
    """
    scrap single page property to return list of dictionary
    """
    single_page_saproperty= []
    
    for property_info_div in properties_info_div:
        property_title_div= property_info_div.find("div", class_= "similar-listings-info").find('h2')
        property_title= property_title_div.get_text() if property_title_div is not None else "N/A"

        listing_type_div= property_info_div.find("div", class_= "similar-listings-info").find('h3')
        listing_type = listing_type_div.get_text() if listing_type_div is not None else "N/A"
        
        property_type_div= property_info_div.find("div", class_= "similar-listings-info").find('h2')
        property_type = property_type_div.get_text() if property_type_div is not None else "N/A"
        
        property_price_div= property_info_div.find("div", class_= "similar-listings-price").find('h4')
        property_price= property_price_div.get_text()if property_price_div is not None else "N/A"  
        
        property_price_currency_div= property_info_div.find("div", class_= "similar-listings-price").find('span')
        property_price_currency= property_price_currency_div.get_text()if property_price_currency_div is not None else "N/A"  

        amenities = property_amenities(property_info_div)
         
        property_location_div= property_info_div.find("div", class_= "similar-listings-info").find('p')
        property_location= property_location_div.get_text()if property_location_div is not None else "N/A" 

        property_agent_name_div = property_info_div.find('div', class_="media").find('img')
        property_agent_name= property_agent_name_div.get('alt') if property_location_div is not None else "N/A"
        
        Property_agent_link_div= property_info_div.find('div', class_='similar-listing-contact').find('a')
        Property_agent_link= Property_agent_link_div.get('href') if Property_agent_link_div is not None else "N/A"
        
        property_date_div = property_info_div.find("div", class_= "media-body").find('h5')
        raw_date = property_date_div.get_text(strip=True) if property_date_div else ""
        dates = normalize_date_div(raw_date)
        
        img_url = extract_image_url(property_info_div)

        favorites_div = property_info_div.find('a', class_="listings-favorite")
        favorites = favorites_div.get('href') if favorites_div is not None else "N/A"

        
    
        single_property = {
            "property_title": property_title,
            "listing_type": listing_type,
            "property_type": property_type,
            "price": property_price,
            "currency": property_price_currency,
            "bedrooms": amenities["bedrooms"],
            "bathrooms": amenities["bathrooms"],
            "toilets": amenities["toilets"],
            "location": property_location,
            "agent_name": property_agent_name,
            "agent_link": Property_agent_link,
            "updated_date": dates["updated_date"],
            "added_date": dates["added_date"],
            "image_url": img_url,
            "favorite": favorites
        }
        single_page_saproperty.append(single_property)
    
    return single_page_saproperty

In [158]:
scrap_page_saproperty(property_info_div)

[{'property_title': 'Distress Two(2)plots Of Land For Sale Rehoboth Park And Gardens, Phase 2 Extension 2, Ibeju Lekki',
  'listing_type': 'RESIDENTIAL LAND For Sale',
  'property_type': 'Distress Two(2)plots Of Land For Sale Rehoboth Park And Gardens, Phase 2 Extension 2, Ibeju Lekki',
  'price': '₦ 45,000,000',
  'currency': '₦',
  'bedrooms': 'N/A',
  'bathrooms': 'N/A',
  'toilets': 'N/A',
  'location': '\n\n\n Close To Dangote Refinery Free Trade Zone Ibeju Lekki Lagos',
  'agent_name': 'Andy Moore Properties',
  'agent_link': '/estate-agents/andymooreproperties',
  'updated_date': '2025-11-30',
  'added_date': '2025-10-15',
  'image_url': 'https://images.privateproperty.com.ng/medium/4-bedroom-terrace-duplex-PvUQ37R3YVqF1YUG9qjN.jpg',
  'favorite': '/profile/add-favorite/48632582'},
 {'property_title': 'Fully Fitted 4 Bedroom Duplex',
  'listing_type': '4 BEDROOM DUPLEX FOR SALE',
  'property_type': 'Fully Fitted 4 Bedroom Duplex',
  'price': '₦ 600,000,000',
  'currency': '₦',
 

In [159]:
len(scrap_page_saproperty(property_info_div))

22

In [162]:
# all properties
all_saproperty = {}

# all pages of website
for page_num in range(1,137):
    # website URL
    URL = f"https://privateproperty.ng/property-for-sale?page={page_num}"
    print(f"Scrapping property data from page {page_num}")

    # make connection
    soup_contents = make_connection_now(URL)

    # single page property 
    properties_info_div = soup_contents.find_all("div", class_="similar-listings-item" )
    
    single_page_saproperty = scrap_page_saproperty(properties_info_div)
    print(f"Property Scrapped successfully: {len(single_page_saproperty)} properties Retrived")

     # sleep
    time.sleep(10)  
    
    all_saproperty.update({f"page {page_num}":single_page_saproperty})

Scrapping property data from page 1
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 2
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 3
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 4
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 5
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 6
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 7
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 8
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 9
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 10
Property Scrapped successfully: 22 properties Retrived
Scrapping property data from page 11
Property Scrapped successfully: 22 properties Retriv

In [163]:
len(all_saproperty)

136

/*
-property_info_div in properties_info_div:
-property_title= property_info_div.find("div", class_= "similar-listings-info").find('h2').get_text()
-listing_type= property_info_div.find("div", class_= "similar-listings-info").find('h3').get_text()
-property_type= property_info_div.find("div", class_= "similar-listings-info").find('h2').get_text()
-property_price= property_info_div.find("div", class_= "similar-listings-price").find('h4').get_text()
-property_price_currency= property_info_div.find("div", class_= "similar-listings-price").find('span').get_text()
-amenities = property_amenities(property_info_div)
-property_location=property_info_div.find("div", class_= "similar-listings-info").find('p').get_text()
-property_agent_name = property_info_div.find('div', class_="media").find('img').get('alt')
-Property_agent_link= property_info_div.find('div', class_='similar-listing-contact').find('a').get('href')
-property_date= property_info_div.find("div", class_= "media-body").find('h5').get_text()
-img_url = extract_image_url(property_info_div)
-favorites = property_info_div.find('a', class_="listings-favorite").get('href') */

# To save it into the json file

In [164]:
# to save the raw data into json file
data_sale = all_saproperty
# Save to JSON
with open("../data/saproperties.json", "w", encoding="utf-8") as f:
    json.dump(data_sale, f, indent=4, ensure_ascii=False)    

In [165]:
# to view the raw data
with open("../data/saproperties.json", "r", encoding="utf-8") as f:
    data_sale = json.load(f)

print(json.dumps(data_sale, indent=4, ensure_ascii=False))

{
    "page 1": [
        {
            "property_title": "Primed 675sqm & 1700sqm Residential Plot In A Beautiful Estate",
            "listing_type": "RESIDENTIAL LAND For Sale",
            "property_type": "Primed 675sqm & 1700sqm Residential Plot In A Beautiful Estate",
            "price": "₦ 340,000,000",
            "currency": "₦",
            "bedrooms": "N/A",
            "bathrooms": "N/A",
            "toilets": "N/A",
            "location": "\n\n\n Victoria Garden City Lekki Lagos",
            "agent_name": "Innerworkings Investment Limited",
            "agent_link": "/estate-agents/innerworkings",
            "updated_date": "2025-11-30",
            "added_date": "2025-07-16",
            "image_url": "https://images.privateproperty.com.ng/medium/4-bedroom-terrace-duplex-PvUQ37R3YVqF1YUG9qjN.jpg",
            "favorite": "/profile/add-favorite/44443662"
        },
        {
            "property_title": "Contemporary 6 Bedroom Detached With 2 Rooms Bq",
            "

In [166]:
# To flattened the pages into a single list instead of showing page number as title

with open("../data/saproperties.json", "r", encoding="utf-8") as f:
    properties_by_page = json.load(f)

# Flatten all pages into one list
all_saproperties = []
for page, listings in properties_by_page.items():
    all_saproperties.extend(listings)

# Save flattened list back into JSON
with open("../data/all_saproperties.json", "w", encoding="utf-8") as f:
    json.dump(all_saproperties, f, indent=4, ensure_ascii=False)


print("Flattened data saved to all_saproperties.json")

# Preview first few results
print(json.dumps(all_saproperties[:5], indent=4, ensure_ascii=False))

Flattened data saved to all_saproperties.json
[
    {
        "property_title": "Primed 675sqm & 1700sqm Residential Plot In A Beautiful Estate",
        "listing_type": "RESIDENTIAL LAND For Sale",
        "property_type": "Primed 675sqm & 1700sqm Residential Plot In A Beautiful Estate",
        "price": "₦ 340,000,000",
        "currency": "₦",
        "bedrooms": "N/A",
        "bathrooms": "N/A",
        "toilets": "N/A",
        "location": "\n\n\n Victoria Garden City Lekki Lagos",
        "agent_name": "Innerworkings Investment Limited",
        "agent_link": "/estate-agents/innerworkings",
        "updated_date": "2025-11-30",
        "added_date": "2025-07-16",
        "image_url": "https://images.privateproperty.com.ng/medium/4-bedroom-terrace-duplex-PvUQ37R3YVqF1YUG9qjN.jpg",
        "favorite": "/profile/add-favorite/44443662"
    },
    {
        "property_title": "Contemporary 6 Bedroom Detached With 2 Rooms Bq",
        "listing_type": "6 BEDROOM DETACHED DUPLEX FOR SALE

In [167]:
# Load the flattened JSON file as a clean table
with open("../data/all_saproperties.json", "r", encoding="utf-8") as f:
    all_saproperties = json.load(f)

# Convert to DataFrame
df = pd.DataFrame(all_saproperties)

# Show the first 10 rows as a table
df.head(10)

property_title  \
0  Primed 675sqm & 1700sqm Residential Plot In A ...   
1    Contemporary 6 Bedroom Detached With 2 Rooms Bq   
2     Contemporary 5 Bedroom Detached With A Room Bq   
3          4 Plot Property With Modern Built Up Hall   
4  Contemporary 5 Bedroom Semi Detached With A Ro...   
5                  5 Bedroom Detached With A Room Bq   
6                      616sqm Prime Residential Land   
7                      515sqm Prime Residential Land   
8                          5 Bedroom Detached Duplex   
9          Fairly New 4 Bedroom Semi Detached Duplex   

                              listing_type  \
0                RESIDENTIAL LAND For Sale   
1       6 BEDROOM DETACHED DUPLEX FOR SALE   
2       5 BEDROOM DETACHED DUPLEX FOR SALE   
3                      EVENT HALL FOR SALE   
4  5 BEDROOM SEMI DETACHED DUPLEX FOR SALE   
5       5 BEDROOM DETACHED DUPLEX FOR SALE   
6                RESIDENTIAL LAND FOR SALE   
7                RESIDENTIAL LAND FOR SALE   
8                5 BEDROOM DUPLEX FOR SALE   
9  4 BEDROOM SEMI DETACHED DUPLEX FOR SALE   

                                       property_type            price  \
0  Primed 675sqm & 1700sqm Residential Plot In A ...    ₦ 340,000,000   
1    Contemporary 6 Bedroom Detached With 2 Rooms Bq      $ 1,700,000   
2     Contemporary 5 Bedroom Detached With A Room Bq  ₦ 2,500,000,000   
3          4 Plot Property With Modern Built Up Hall    ₦ 400,000,000   
4  Contemporary 5 Bedroom Semi Detached With A Ro...    ₦ 850,000,000   
5                  5 Bedroom Detached With A Room Bq  ₦ 1,600,000,000   
6                      616sqm Prime Residential Land    ₦ 780,000,000   
7                      515sqm Prime Residential Land    ₦ 680,000,000   
8                          5 Bedroom Detached Duplex    ₦ 800,000,000   
9          Fairly New 4 Bedroom Semi Detached Duplex    ₦ 200,000,000   

  currency bedrooms bathrooms toilets  \
0        ₦      N/A       N/A     N/A   
1        $        6         6       7   
2        ₦        5         5       6   
3        ₦      N/A         3       9   
4        ₦        5         5       6   
5        ₦        5         5       6   
6        ₦      N/A       N/A     N/A   
7        ₦      N/A       N/A     N/A   
8        ₦        5         5       6   
9        ₦        4       N/A     N/A   

                                            location  \
0            \n\n\n Victoria Garden City Lekki Lagos   
1                       \n\n\n Old Ikoyi Ikoyi Lagos   
2  \n\n\n Spa Road, Ikate Ikate Elegushi Lekki Lagos   
3  \n\n\n Olusegun Osoba Road Iju Ogundimu Ifako ...   
4  \n\n\n Spa Road, Ikate Ikate Elegushi Lekki Lagos   
5              \n\n\n Osapa London Osapa Lekki Lagos   
6      \n\n\n Pinnock Beach Estate Osapa Lekki Lagos   
7      \n\n\n Pinnock Beach Estate Osapa Lekki Lagos   
8  \n\n\n Freedom Way Lekki Phase 1 Lekki Phase 1...   
9                                 \n\n\n Ikeja Lagos   

                         agent_name                             agent_link  \
0  Innerworkings Investment Limited           /estate-agents/innerworkings   
1           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
2           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
3         Business Growth Services   /estate-agents/businessgrowthservices   
4           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
5           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
6           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
7           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
8           Stalwart Morgan Limited       /estate-agents/stalwartmorganltd   
9                 Benjoy Properties        /estate-agents/benjoyproperties   

  updated_date  added_date                                          image_url  \
0   2025-11-30  2025-07-16  https://images.privateproperty.com.ng/medium/4...   
1   2025-12-02      